In [1]:
import numpy as np
import pandas as pd
import torch
from bioservices import UniProt
import requests

In [2]:
df=pd.read_csv("masterDatabaseall3.tsv",sep="\t")
dfall3=df

In [ ]:
#df["Substrate_Acc_Noiso"]=df["Substrate_Acc"].str.split("-").str[0]

In [7]:
df[df["Substrate_Acc"]=="Q8WZ42-3"]

Substrate Substrate_Acc   Motif_Sequence  position Kinase Kinase_Acc  \
30524       NaN      Q8WZ42-3  YEITAANSSGTTKAF     20057   SIK1     P57059   
30686       NaN      Q8WZ42-3  INLKESVTADAGRYE     20044   SIK1     P57059   
30687       NaN      Q8WZ42-3  DAGRYEITAANSSGT     20053   SIK1     P57059   

      kinase_group kinase_family kinase_sub_family  binding_domain  \
30524         CAMK         CAMKL               QIK             NaN   
30686         CAMK         CAMKL               QIK             NaN   
30687         CAMK         CAMKL               QIK             NaN   

       taxonomy_id species_name    db_source  SIGNOR_Score  
30524         9606          NaN  KINASE-iKiP           NaN  
30686         9606          NaN  KINASE-iKiP           NaN  
30687         9606          NaN  KINASE-iKiP           NaN

In [4]:
len(df["Substrate_Acc"].unique()) #get unique substrate identifiers

6652

In [ ]:
#len(df["Substrate_Acc_Noiso"].unique()) # unique substrate identifiers if we disregard isoforms

5522

In [8]:
uniqacc=list(df["Substrate_Acc"].unique()) #convert array of unique entries to list

In [6]:
len([str for str in uniqacc if str[-2]=="-"]) # 1058 isoform entries

1058

In [9]:

def fetch_uniprot_sequences(accessions):
    base_url = "https://rest.uniprot.org/uniprotkb/{}.fasta"
    sequences = {}

    for acc in accessions:
        url = base_url.format(acc)
        response = requests.get(url)
        if response.ok:
            fasta = response.text
            lines = fasta.splitlines()
            sequence = ''.join(lines[1:])  # Remove FASTA header
            sequences[acc] = sequence
        else:
            print(f"Failed to fetch {acc}: {response.status_code}")
            sequences[acc] = None

    return sequences


accession_list = uniqacc
sequences = fetch_uniprot_sequences(accession_list)

for acc, seq in sequences.items():
    print(f">{acc}\n{seq}\n")

Failed to fetch ENSP00000267569: 400
Failed to fetch ENSP00000357298: 400
Failed to fetch ENSP00000261937: 400
Failed to fetch ENSP00000352232: 400
Failed to fetch ENSP00000248996: 400
Failed to fetch ENSP00000357225: 400
Failed to fetch ENSP00000347528: 400
Failed to fetch ENSP00000248419: 400
Failed to fetch ENSP00000328213: 400
Failed to fetch ENSP00000343690: 400
Failed to fetch ENSMUSP00000007980: 400
Failed to fetch ENSMUSP00000034815: 400
Failed to fetch ENSMUSP00000098874: 400
Failed to fetch ENSMUSP00000050824: 400
Failed to fetch ENSMUSP00000043430: 400
Failed to fetch ENSMUSP00000029545: 400
Failed to fetch ENSRNOP00000013522: 400
Failed to fetch ENSRNOP00000012056: 400
Failed to fetch ENSRNOP00000048410: 400
Failed to fetch P18433-2: 404
Failed to fetch AAC50053: 400
Failed to fetch NP_001184222: 400
Failed to fetch O60504_VAR_055019: 400
Failed to fetch Q12809_VAR_014388: 400
Failed to fetch O15320-8: 404
Failed to fetch P40855-5: 404
Failed to fetch XP_001480843: 400
Fail

In [ ]:
sum(1 for v in sequences.values() if v is None) # 29 failed entries

29

In [209]:
[len(v) if v is not None else 0 for v in sequences.values()][2666]

34350

In [208]:
np.argmax([len(v) if v is not None else 0 for v in sequences.values()])

2666

In [210]:
sequences.get("P16885")

'MSTTVNVDSLAEYEKSQIKRALELGTVMTVFSFRKSTPERRTVQVIMETRQVAWSKTADKIEGFLDIMEIKEIRPGKNSKDFERAKAVRQKEDCCFTILYGTQFVLSTLSLAADSKEDAVNWLSGLKILHQEAMNASTPTIIESWLRKQIYSVDQTRRNSISLRELKTILPLINFKVSSAKFLKDKFVEIGAHKDELSFEQFHLFYKKLMFEQQKSILDEFKKDSSVFILGNTDRPDASAVYLHDFQRFLIHEQQEHWAQDLNKVRERMTKFIDDTMRETAEPFLFVDEFLTYLFSRENSIWDEKYDAVDMQDMNNPLSHYWISSSHNTYLTGDQLRSESSPEAYIRCLRMGCRCIELDCWDGPDGKPVIYHGWTRTTKIKFDDVVQAIKDHAFVTSSFPVILSIEEHCSVEQQRHMAKAFKEVFGDLLLTKPTEASADQLPSPSQLREKIIIKHKKLGPRGDVDVNMEDKKDEHKQQGELYMWDSIDQKWTRHYCAIADAKLSFSDDIEQTMEEEVPQDIPPTELHFGEKWFHKKVEKRTSAEKLLQEYCMETGGKDGTFLVRESETFPNDYTLSFWRSGRVQHCRIRSTMEGGTLKYYLTDNLTFSSIYALIQHYRETHLRCAEFELRLTDPVPNPNPHESKPWYYDSLSRGEAEDMLMRIPRDGAFLIRKREGSDSYAITFRARGKVKHCRINRDGRHFVLGTSAYFESLVELVSYYEKHSLYRKMRLRYPVTPELLERYNMERDINSLYDVSRMYVDPSEINPSMPQRTVKALYDYKAKRSDELSFCRGALIHNVSKEPGGWWKGDYGTRIQQYFPSNYVEDISTADFEELEKQIIEDNPLGSLCRGILDLNTYNVVKAPQGKNQKSFVFILEPKQQGDPPVEFATDRVEELFEWFQSIREITWKIDTKENNMKYWEKNQSIAIELSDLVVYCKPTSKTKDNLENPDFREIRSFVETKADSIIRQKPVDLLKYNQKGLTRVYPKGQRVDSSNYDP

In [211]:
ll=[]
max=8196
for key,seq in sequences.items():
   
    if seq is None:
        ll+=[0]
    else:
        if len(seq)>max:
            print(key)
        ll+=[len(seq)]
    

Q8WZ42
Q8WZ42-3


In [212]:
np.argmax(ll)

2666

In [6]:
sequences.get("SIGNOR-C545")

NameError: name 'sequences' is not defined

In [11]:
df["Substrate_Acc"].apply(lambda x: sequences.get(x)) #apply the dictionary mapping to the sequence

0        MGCVQCKDKEATKLTEERDGSLNQSSGYRYGTDPTPQHYPSFGVTS...
1        MTAKMETTFYDDALNASFLPSESGPYGYSNPKILKQSMTLNLADPV...
2        MPEETQTQDQPMEEEEVETFAFQAEIAQLMSLIINTFYSNKEIFLR...
3        MATGGRRGAAAAPLLVAVAALLLGAAGHLYPGEVCPGMDIRNNLTR...
4        MATVEPETTPTPNPPTTEEEKTESNQEVANPEHYIKHPLQNRWALW...
                               ...                        
57300    MASGRPEELWEAVVGAAERFRARTGTELVLLTAAPPPPPRPGPCAY...
57301    MKLNISFPATGCQKLIEVDDERKLRTFYEKRMATEVAADALGEEWK...
57302    MAEAPASPVPLSPLEVELDPEFEPQSRPRSCTWPLQRPELQASPAK...
57303    METPSQRRPTRSGAQASSTPLSPTRITRLQEKEDLQELNDRLAVYI...
57304    MEKVQYLTRSAIRRASTIEMPQQARQNLQNLFINFCLILICLLLIC...
Name: Substrate_Acc, Length: 57305, dtype: object

In [12]:
df["Full_Sequence"]=df["Substrate_Acc"].apply(lambda x: sequences.get(x))

In [217]:
df[df["Substrate_Acc"]=="Q8WZ42"]

Substrate Substrate_Acc   Motif_Sequence  position  Kinase Kinase_Acc  \
15652       NaN        Q8WZ42  SEQPGLFSEWLRNIE      4099   PRKG1     Q13976   
15668       NaN        Q8WZ42  IQQGAKTSLQEEMDS      4185   PRKG1     Q13976   
15674       NaN        Q8WZ42  ALQAAVASEQPGLFS      4092   PRKG1     Q13976   
15679       NaN        Q8WZ42  VRIEEGKSLRFPLAL      4010   PRKG1     Q13976   
15681       NaN        Q8WZ42  KEEVVLKSVLRKRPE     11878   PRKG1     Q13976   
16502       NaN        Q8WZ42  RRKLRPGSGGEKPPD     12022   PRKCA     P17252   
16688       NaN        Q8WZ42  KEEVVLKSVLRKRPE     11878   PRKCA     P17252   
17131       NaN        Q8WZ42  RDLLSKESLLSGIPE      4065  PRKACA     P17612   
17139       NaN        Q8WZ42  IQQGAKTSLQEEMDS      4185  PRKACA     P17612   
17272       NaN        Q8WZ42  VRIEEGKSLRFPLAL      4010  PRKACA     P17612   
24973       NaN        Q8WZ42  EVEVPTVTKRERKIP     11922  CAMK2D     Q13557   
24977       NaN        Q8WZ42  RRKLRPGSGGEKPPD     12022  CAMK2D     Q13557   
24979       NaN        Q8WZ42  ERKIPEPTKVPEIKP     11932  CAMK2D     Q13557   
24980       NaN        Q8WZ42  PPVEPEPTPIAAPVT     11969  CAMK2D     Q13557   
24984       NaN        Q8WZ42  KEEVVLKSVLRKRPE     11878  CAMK2D     Q13557   

      kinase_group kinase_family kinase_sub_family  binding_domain  \
15652          AGC           PKG               NaN             NaN   
15668          AGC           PKG               NaN             NaN   
15674          AGC           PKG               NaN             NaN   
15679          AGC           PKG               NaN             NaN   
15681          AGC           PKG               NaN             NaN   
16502          AGC           PKC              PKCA             NaN   
16688          AGC           PKC              PKCA             NaN   
17131          AGC           PKA               NaN             NaN   
17139          AGC           PKA               NaN             NaN   
17272          AGC           PKA               NaN             NaN   
24973         CAMK         CAMK2               NaN             NaN   
24977         CAMK         CAMK2               NaN             NaN   
24979         CAMK         CAMK2               NaN             NaN   
24980         CAMK         CAMK2               NaN             NaN   
24984         CAMK         CAMK2               NaN             NaN   

       taxonomy_id species_name   db_source  SIGNOR_Score  \
15652         9606          NaN  KINASE-PSP           NaN   
15668         9606          NaN  KINASE-PSP           NaN   
15674         9606          NaN  KINASE-PSP           NaN   
15679         9606          NaN  KINASE-PSP           NaN   
15681         9606          NaN  KINASE-PSP           NaN   
16502         9606          NaN  KINASE-PSP           NaN   
16688         9606          NaN  KINASE-PSP           NaN   
17131         9606          NaN  KINASE-PSP           NaN   
17139         9606          NaN  KINASE-PSP           NaN   
17272         9606          NaN  KINASE-PSP           NaN   
24973         9606          NaN  KINASE-PSP           NaN   
24977         9606          NaN  KINASE-PSP           NaN   
24979         9606          NaN  KINASE-PSP           NaN   
24980         9606          NaN  KINASE-PSP           NaN   
24984         9606          NaN  KINASE-PSP           NaN   

                                           Full_Sequence  
15652  MTTQAPTFTQPLQSVVVLEGSTATFEAHISGFPVPEVSWFRDGQVI...  
15668  MTTQAPTFTQPLQSVVVLEGSTATFEAHISGFPVPEVSWFRDGQVI...  
15674  MTTQAPTFTQPLQSVVVLEGSTATFEAHISGFPVPEVSWFRDGQVI...  
15679  MTTQAPTFTQPLQSVVVLEGSTATFEAHISGFPVPEVSWFRDGQVI...  
15681  MTTQAPTFTQPLQSVVVLEGSTATFEAHISGFPVPEVSWFRDGQVI...  
16502  MTTQAPTFTQPLQSVVVLEGSTATFEAHISGFPVPEVSWFRDGQVI...  
16688  MTTQAPTFTQPLQSVVVLEGSTATFEAHISGFPVPEVSWFRDGQVI...  
17131  MTTQAPTFTQPLQSVVVLEGSTATFEAHISGFPVPEVSWFRDGQVI...  
17139  MTTQAPTFTQPLQSVVVLEGSTATFEAHISGFPVPEVSWFRDGQVI...  
17272  MTTQAPTFTQPLQSVVVLEGSTATFEAHISGFPVPEVSWFRDGQVI

In [ ]:
df[df["Full_Sequence"].isna()] #89 sequences are None (29 different proteins)

Substrate    Substrate_Acc   Motif_Sequence  position  Kinase  \
1489        NaN  ENSP00000267569  VRTDSVKTPESEGNP       148   MAPK9   
1490        NaN  ENSP00000267569  VRTDSVKTPESEGNP       148  MAPK14   
2333        NaN  ENSP00000357298  PVDPRRRSLPAGDAL       887    PAK1   
2692        NaN  ENSP00000261937  FPMTPTTYKGSVDNQ      1265     KDR   
3008        NaN  ENSP00000352232  VHPLSAPYPPLDTPE       494    JAK1   
...         ...              ...              ...       ...     ...   
56104       NaN     XP_001480843  RLVEQLLSPRTQAQR        17    CDK5   
56600       NaN     XP_006230684  GFEYQGKTEKHASQK       145   PRKCA   
56634       NaN     XP_006230684  QMDRVDQSAVGFEYQ       135   PRKCA   
56649       NaN     XP_006230684  QADRVDKSAVGFDYQ       172   PRKCA   
56875       NaN     NP_001258431  RTSTAPSSPGVDSVP       444   MAPK8   

      Kinase_Acc kinase_group kinase_family kinase_sub_family  binding_domain  \
1489      P45984         CMGC          MAPK               JNK             NaN   
1490      Q16539         CMGC          MAPK               P38             NaN   
2333      Q13153          STE         STE20              PAKA             NaN   
2692      P35968           TK         VEGFR               NaN             NaN   
3008      P23458           TK           JAK               NaN             NaN   
...          ...          ...           ...               ...             ...   
56104     Q00535         CMGC           CDK              CDK5             NaN   
56600     P17252          AGC           PKC              PKCA             NaN   
56634     P17252          AGC           PKC              PKCA             NaN   
56649     P17252          AGC           PKC              PKCA             NaN   
56875     P45983         CMGC          MAPK               JNK             NaN   

       taxonomy_id  species_name   db_source  SIGNOR_Score Full_Sequence  
1489          9606  Homo sapiens  phosphoELM           NaN          None  
1490          9606  Homo sapiens  phosphoELM           NaN          None  
2333          9606  Homo sapiens  phosphoELM           NaN          None  
2692          9606  Homo sapiens  phosphoELM           NaN          None  
3008          9606  Homo sapiens  phosphoELM           NaN          None  
...            ...           ...         ...           ...           ...  
56104        10090           NaN  KINASE-PSP           NaN          None  
56600        10116           NaN  KINASE-PSP           NaN          None  
56634        10116           NaN  KINASE-PSP           NaN          None  
56649        10116           NaN  KINASE-PSP           NaN          None  
56875        10116           NaN  KINASE-PSP           NaN          None  

[89 rows x 15 columns]

In [13]:
df_deduplicated=df.drop_duplicates(subset=["Substrate_Acc","Motif_Sequence","position","Kinase_Acc"])

In [ ]:
#construct df for mouse and rat
df_deduplicated_mouse=df_deduplicated[df_deduplicated["taxonomy_id"]==10090]
df_deduplicated_rat=df_deduplicated[df_deduplicated["taxonomy_id"]==10116]
df_deduplicated_mouse_noNAseq=df_deduplicated_mouse.dropna(subset="Full_Sequence")
df_deduplicated_rat_noNAseq=df_deduplicated_rat.dropna(subset="Full_Sequence")

In [ ]:
df_deduplicated_human=df_deduplicated[df_deduplicated["taxonomy_id"]==9606]

In [19]:
df_deduplicated_mouse_noNAseq.to_csv("ESM-2/deduplicated_mouse_fullSeq.tsv", sep='\t',index=False)
df_deduplicated_rat_noNAseq.to_csv("ESM-2/deduplicated_rat_fullSeq.tsv", sep="\t", index = False)

In [2]:
dfloadm=pd.read_csv("ESM-2/deduplicated_mouse_fullSeq.tsv", sep='\t')
dfloadr=pd.read_csv("ESM-2/deduplicated_rat_fullSeq.tsv", sep='\t')
dfloadm=dfloadm.dropna(subset=["Full_Sequence"])
dfloadr=dfloadr.dropna(subset=["Full_Sequence"])

In [221]:
df_deduplicated_human

Substrate Substrate_Acc   Motif_Sequence  position Kinase Kinase_Acc  \
0           NaN        P06241  TDPTPQHYPSFGVTS        39    FYN     P06241   
1           NaN        P05412  VPEMPGETPPLSPID       239  GSK3A     P49840   
2           NaN        P07900  PEIEDVGSDEEEEKK       263    NaN        NaN   
3           NaN        P06213  SLGFKRSYEEHIPYT      1355   INSR     P06213   
4           NaN        P06730  DTATKSGSTTKNRFV       209   MNK1     Q9BUB5   
...         ...           ...              ...       ...    ...        ...   
54484       NaN      Q92734-2  YTQPGPGYR______       395   ABL2     P42684   
54485       NaN      Q96HC4-7  VERYTEFYHVPTHSD       148   ABL2     P42684   
54486       NaN        Q9BTC0  KALGSAQYEDPRNLH      1700   ABL2     P42684   
54487       NaN        Q9H3P7  RDCHEEVYAGSHQYP       492   ABL2     P42684   
54488       NaN        Q9NUQ9  TESEKEIYNQVNVVL        36   ABL2     P42684   

      kinase_group kinase_family kinase_sub_family  binding_domain  \
0               TK           SRC               NaN             NaN   
1             CMGC           GSK               NaN             NaN   
2             CMGC           CK2               NaN             NaN   
3               TK          INSR               NaN             NaN   
4             CAMK       MAPKAPK               MNK             NaN   
...            ...           ...               ...             ...   
54484           TK           ABL               NaN             NaN   
54485           TK           ABL               NaN             NaN   
54486           TK           ABL               NaN             NaN   
54487           TK           ABL               NaN             NaN   
54488           TK           ABL               NaN             NaN   

       taxonomy_id  species_name    db_source  SIGNOR_Score  \
0             9606  Homo sapiens   phosphoELM           NaN   
1             9606  Homo sapiens   phosphoELM           NaN   
2             9606  Homo sapiens   phosphoELM           NaN   
3             9606  Homo sapiens   phosphoELM           NaN   
4             9606  Homo sapiens   phosphoELM           NaN   
...            ...           ...          ...           ...   
54484         9606           NaN  KINASE-iKiP           NaN   
54485         9606           NaN  KINASE-iKiP           NaN   
54486         9606           NaN  KINASE-iKiP           NaN   
54487         9606           NaN  KINASE-iKiP           NaN   
54488         9606           NaN  KINASE-iKiP           NaN   

                                           Full_Sequence  
0      MGCVQCKDKEATKLTEERDGSLNQSSGYRYGTDPTPQHYPSFGVTS...  
1      MTAKMETTFYDDALNASFLPSESGPYGYSNPKILKQSMTLNLADPV...  
2      MPEETQTQDQPMEEEEVETFAFQAEIAQLMSLIINTFYSNKEIFLR...  
3      MATGGRRGAAAAPLLVAVAALLLGAAGHLYPGEVCPGMDIRNNLTR...  
4      MATVEPETTPTPNPPTTEEEKTESNQEVANPEHYIKHPLQNRWALW...  
...                                                  ...  
54484  MNGQLDLSGKLIIKAQLGEDIRRIPIHNEDITYDELVLMMQRVFRG...  
54485  MSNYSVSLVGPAPWGFRLQGGKDFNMPLTISSLKDGGKAAQANVRI...  
54486  MDDKGDPSNEEAPKAIKPTSKEFRKTWGFRRTTIAKREGAGDAEAD...  
54487  MAAVLNAERLEVSVDGLTLSPDPEERPGAEGAPLLPPPLPPPSPPG...  
54488  MGNLLKVLTCTDLEQGPNFFLDFENAQPTESEKEIYNQVNVVLKDA...  

[46754 rows x 15 columns]

In [222]:
df_deduplicated_human_noNAseq=df_deduplicated_human.dropna(subset="Full_Sequence")

In [223]:
df_deduplicated_human_noNAseq[df_deduplicated_human_noNAseq["Substrate_Acc"]=="P62158"] #FULL SEQEUNCE BEING NONE IS NOT FILTERED OUT! When loading the df back in new NaNs will be created.

Substrate Substrate_Acc   Motif_Sequence  position Kinase Kinase_Acc  \
628       NaN        P62158  MARKMKDTDSEEEIR        80    NaN        NaN   
629       NaN        P62158  FDKDGNGYISAAELR       100   EGFR     P00533   
630       NaN        P62158  FDKDGNGYISAAELR       100   INSR     P06213   
632       NaN        P62158  KDGNGYISAAELRHV       102    NaN        NaN   

    kinase_group kinase_family kinase_sub_family  binding_domain  taxonomy_id  \
628         CMGC           CK2               NaN             NaN         9606   
629           TK          EGFR               NaN             NaN         9606   
630           TK          INSR               NaN             NaN         9606   
632         CMGC           CK2               NaN             NaN         9606   

     species_name   db_source  SIGNOR_Score Full_Sequence  
628  Homo sapiens  phosphoELM           NaN                
629  Homo sapiens  phosphoELM           NaN                
630  Homo sapiens  phosphoELM           NaN                
632  Homo sapiens  phosphoELM           NaN

In [ ]:
#df_deduplicated_human_noNAseq.to_csv("ESM-2/deduplicated_human_fullSeq.tsv", sep='\t',index=False)

In [4]:
dfload=pd.read_csv("ESM-2/deduplicated_human_fullSeq.tsv", sep='\t')

In [28]:
dfload[dfload["Full_Sequence"].isna()]

Substrate Substrate_Acc   Motif_Sequence  position   Kinase Kinase_Acc  \
481         NaN        P01233  QCALCRRSTTDCGGP       116      NaN        NaN   
527         NaN        P62158  MARKMKDTDSEEEIR        80      NaN        NaN   
528         NaN        P62158  FDKDGNGYISAAELR       100     EGFR     P00533   
529         NaN        P62158  FDKDGNGYISAAELR       100     INSR     P06213   
530         NaN        P62158  KDGNGYISAAELRHV       102      NaN        NaN   
776         NaN        P01233  YRDVRFESIRLPGCP        86      NaN        NaN   
777         NaN        P01233  CALCRRSTTDCGGPK       117      NaN        NaN   
11132       NaN        P62988  DYNIQKESTLHLVLR        65    PINK1     Q9BXM7   
11139       NaN        P62988  YNIQKESTLHLVLRL        66    PINK1     Q9BXM7   
19731       NaN        P0DN76  _MAEYLASIFGTEKD         7      ZAK     Q9NYL2   
19788       NaN        P0DN76  YLASIFGTEKDKVNC        11      ZAK     Q9NYL2   
22255       NaN        P0DN76  _MAEYLASIFGTEKD         7     STK3     Q13188   
22320       NaN        P0DN76  YLASIFGTEKDKVNC        11     STK3     Q13188   
22420       NaN        P0DN76  _MAEYLASIFGTEKD         7    STK26     Q9P289   
22496       NaN        P0DN76  YLASIFGTEKDKVNC        11    STK26     Q9P289   
24609       NaN        P0DN76  ____MAEYLASIFGT         4     ROS1     P08922   
24894       NaN        P0DN76  ____MAEYLASIFGT         4      RET     P07949   
29260       NaN        P0DN76  _MAEYLASIFGTEKD         7     NEK1     Q96PY6   
29334       NaN        P0DN76  YLASIFGTEKDKVNC        11     NEK1     Q96PY6   
35114       NaN        P0DN76  _MAEYLASIFGTEKD         7  MAP3K10     Q02779   
35166       NaN        P0DN76  YLASIFGTEKDKVNC        11  MAP3K10     Q02779   
36234       NaN        P0DN76  ____MAEYLASIFGT         4     JAK2     O60674   
36531       NaN        P0DN76  ____MAEYLASIFGT         4     INSR     P06213   
36825       NaN        P0DN76  ____MAEYLASIFGT         4    IGF1R     P08069   
37953       NaN        P0DN76  ____MAEYLASIFGT         4     FLT3     P36888   
38228       NaN        P0DN76  ____MAEYLASIFGT         4    FGFR2     P21802   
38307       NaN        P0DN76  ____MAEYLASIFGT         4    FGFR1     P11362   
38421       NaN        P0DN76  ____MAEYLASIFGT         4      FES     P07332   
39047       NaN        P0DN76  ____MAEYLASIFGT         4    EPHB2     P29323   
39292       NaN        P0DN76  ____MAEYLASIFGT         4    EPHA8     P29322   
39649       NaN        P0DN76  ____MAEYLASIFGT         4    EPHA3     P29320   

      kinase_group kinase_family kinase_sub_family  binding_domain  \
481            AGC           PKA               NaN             NaN   
527           CMGC           CK2               NaN             NaN   
528             TK          EGFR               NaN             NaN   
529             TK          INSR               NaN             NaN   
530           CMGC           CK2               NaN             NaN   
776            AGC           PKA               NaN             NaN   
777            AGC           PKA               NaN             NaN   
11132        OTHER          NKF2               NaN             NaN   
11139        OTHER          NKF2               NaN             NaN   
19731          TKL           MLK               ZAK             NaN   
19788          TKL           MLK               ZAK             NaN   
22255          STE         STE20               MST             NaN   
22320          STE         STE20               MST             NaN   
22420          STE         STE20               YSK             NaN   
22496          STE         STE20               YSK             NaN   
24609           TK           SEV               NaN             NaN   
24894           TK           RET               NaN             NaN   
29260        OTHER           NEK               NaN             NaN   
29334        OTHER           NEK               NaN             NaN   
35114          TKL           MLK             

In [5]:
dfload=dfload.dropna(subset=["Full_Sequence"])

In [48]:
#potential issue, same substrate identifier as the human in mice and rat, will have to remove substrates
print(np.sum(dfloadm["Substrate_Acc"].isin(dfload["Substrate_Acc"])),"of the substrate entries in mouse appear also in human")
print(np.sum(dfloadr["Substrate_Acc"].isin(dfload["Substrate_Acc"])),"of the substrate entries in rat appear also in human")

1143 of the substrate entries in mouse appear also in human
69 of the substrate entries in rat appear also in human


In [ ]:
# using position and substrate acc to not disqualify all substrates that were seen
dfloadm[~dfloadm[["Substrate_Acc", "position"]].apply(tuple, axis=1).isin(
    dfload[["Substrate_Acc", "position"]].apply(tuple, axis=1)
)]

Substrate Substrate_Acc   Motif_Sequence  position Kinase Kinase_Acc  \
0          NaN        O08605  RKTRATDSLPGKFED        39   PAK2     Q13177   
1          NaN        O08605  RRKKKRKTRATDSLP        34   PAK2     Q13177   
4          NaN        Q62101  KALSERVSIL_____       916   PKD1     Q15139   
8          NaN        Q61792  SSSYRRPTEQQQPQP       156   PKG1     Q13976   
9          NaN        Q61410  LDVHRKTSGLVSLHS       110   PKG2     Q13237   
...        ...           ...              ...       ...    ...        ...   
2189       NaN        P28867  TTESVGIYQGFEKKP       311   ABL1     P00519   
2190       NaN        F2Z3U3  GGSHISGYATLRRGP      1242   ABL1     P00519   
2191       NaN        Q60598  TYTSEPVYETTEAPG       466   ABL1     P00519   
2193       NaN        O88809  ELEEGESYVCSSDNF       125   ABL1     P00519   
2194       NaN        Q8BH43  GKEALKFYTNPSYFF       150   ABL1     P00519   

     kinase_group kinase_family kinase_sub_family  binding_domain  \
0             STE         STE20              PAKA             NaN   
1             STE         STE20              PAKA             NaN   
4            CAMK           PKD               NaN             NaN   
8             AGC           PKG               NaN             NaN   
9             AGC           PKG               NaN             NaN   
...           ...           ...               ...             ...   
2189           TK           ABL               NaN             NaN   
2190           TK           ABL               NaN             NaN   
2191           TK           ABL               NaN             NaN   
2193           TK           ABL               NaN             NaN   
2194           TK           ABL               NaN             NaN   

      taxonomy_id  species_name   db_source  SIGNOR_Score  \
0           10090  Mus musculus  phosphoELM           NaN   
1           10090  Mus musculus  phosphoELM           NaN   
4           10090  Mus musculus  phosphoELM           NaN   
8           10090  Mus musculus  phosphoELM           NaN   
9           10090  Mus musculus  phosphoELM           NaN   
...           ...           ...         ...           ...   
2189        10090           NaN  KINASE-PSP           NaN   
2190        10090           NaN  KINASE-PSP           NaN   
2191        10090           NaN  KINASE-PSP           NaN   
2193        10090           NaN  KINASE-PSP           NaN   
2194        10090           NaN  KINASE-PSP           NaN   

                                          Full_Sequence  
0     MVSSQKLEKPIEMGSSEPLPIVDSDKRRKKKRKTRATDSLPGKFED...  
1     MVSSQKLEKPIEMGSSEPLPIVDSDKRRKKKRKTRATDSLPGKFED...  
4     MSVPPLLRPPSPLLPAAAAVAAAAAALVPGSGPAPFPAPGAAPAGG...  
8     MNPNCARCGKIVYPTEKVNCLDKYWHKACFHCETCKMTLNMKNYKG...  
9     MGNGSVKPKHAKHPDGHSGNLSNEALRSKVLELERELRRKDAELQE...  
...                                                 ...  
2189  MAPFLRISFNSYELGSLQVEDEASQPFCAVKMKEALSTERGKTLVQ...  
2190  MEQLSDEEIDHGAEEDSDKEDQDLDKMFGAWLGELDRLTQSLDSDK...  
2191  MWKASAGHAVSITQDDGGADDWETDPDFVNDVSEKEQRWGAKTVQG...  
2193  MELDFGHFDERDKASRNMRGSRMNGLPSPTHSAHCSFYRTRTLQAL...  
2194  MPLVTRNIEPRHLCRQTLPSDTSELECRTNITLANVIRQLGSLSKY...  

[1765 rows x 15 columns]

In [10]:
dfloadm

Substrate Substrate_Acc   Motif_Sequence  position Kinase Kinase_Acc  \
0          NaN        O08605  RKTRATDSLPGKFED        39   PAK2     Q13177   
1          NaN        O08605  RRKKKRKTRATDSLP        34   PAK2     Q13177   
4          NaN        Q62101  KALSERVSIL_____       916   PKD1     Q15139   
8          NaN        Q61792  SSSYRRPTEQQQPQP       156   PKG1     Q13976   
9          NaN        Q61410  LDVHRKTSGLVSLHS       110   PKG2     Q13237   
...        ...           ...              ...       ...    ...        ...   
2189       NaN        P28867  TTESVGIYQGFEKKP       311   ABL1     P00519   
2190       NaN        F2Z3U3  GGSHISGYATLRRGP      1242   ABL1     P00519   
2191       NaN        Q60598  TYTSEPVYETTEAPG       466   ABL1     P00519   
2193       NaN        O88809  ELEEGESYVCSSDNF       125   ABL1     P00519   
2194       NaN        Q8BH43  GKEALKFYTNPSYFF       150   ABL1     P00519   

     kinase_group kinase_family kinase_sub_family  binding_domain  \
0             STE         STE20              PAKA             NaN   
1             STE         STE20              PAKA             NaN   
4            CAMK           PKD               NaN             NaN   
8             AGC           PKG               NaN             NaN   
9             AGC           PKG               NaN             NaN   
...           ...           ...               ...             ...   
2189           TK           ABL               NaN             NaN   
2190           TK           ABL               NaN             NaN   
2191           TK           ABL               NaN             NaN   
2193           TK           ABL               NaN             NaN   
2194           TK           ABL               NaN             NaN   

      taxonomy_id  species_name   db_source  SIGNOR_Score  \
0           10090  Mus musculus  phosphoELM           NaN   
1           10090  Mus musculus  phosphoELM           NaN   
4           10090  Mus musculus  phosphoELM           NaN   
8           10090  Mus musculus  phosphoELM           NaN   
9           10090  Mus musculus  phosphoELM           NaN   
...           ...           ...         ...           ...   
2189        10090           NaN  KINASE-PSP           NaN   
2190        10090           NaN  KINASE-PSP           NaN   
2191        10090           NaN  KINASE-PSP           NaN   
2193        10090           NaN  KINASE-PSP           NaN   
2194        10090           NaN  KINASE-PSP           NaN   

                                          Full_Sequence  
0     MVSSQKLEKPIEMGSSEPLPIVDSDKRRKKKRKTRATDSLPGKFED...  
1     MVSSQKLEKPIEMGSSEPLPIVDSDKRRKKKRKTRATDSLPGKFED...  
4     MSVPPLLRPPSPLLPAAAAVAAAAAALVPGSGPAPFPAPGAAPAGG...  
8     MNPNCARCGKIVYPTEKVNCLDKYWHKACFHCETCKMTLNMKNYKG...  
9     MGNGSVKPKHAKHPDGHSGNLSNEALRSKVLELERELRRKDAELQE...  
...                                                 ...  
2189  MAPFLRISFNSYELGSLQVEDEASQPFCAVKMKEALSTERGKTLVQ...  
2190  MEQLSDEEIDHGAEEDSDKEDQDLDKMFGAWLGELDRLTQSLDSDK...  
2191  MWKASAGHAVSITQDDGGADDWETDPDFVNDVSEKEQRWGAKTVQG...  
2193  MELDFGHFDERDKASRNMRGSRMNGLPSPTHSAHCSFYRTRTLQAL...  
2194  MPLVTRNIEPRHLCRQTLPSDTSELECRTNITLANVIRQLGSLSKY...  

[1765 rows x 15 columns]

In [6]:
#remove entries that are missclassified in signor
dfloadm=dfloadm[~dfloadm[["Substrate_Acc", "position"]].apply(tuple, axis=1).isin(dfload[["Substrate_Acc", "position"]].apply(tuple, axis=1))]
dfloadr=dfloadr[~dfloadr[["Substrate_Acc", "position"]].apply(tuple, axis=1).isin(dfload[["Substrate_Acc", "position"]].apply(tuple, axis=1))]

In [70]:
dfloadr

Substrate Substrate_Acc   Motif_Sequence  position Kinase Kinase_Acc  \
0          NaN        P08050  TAPLSPMSPPGYKLV       282  MAPK3     P27361   
1          NaN        P43884  PSLLRRVSTLANTLS       223    NaN        NaN   
2          NaN        P08050  SSPTAPLSPMSPPGY       279  MAPK3     P27361   
3          NaN        P35570  NRKGNGDYMPMSPKS       628  IGF1R     P08069   
4          NaN        P43884  EPVVRRLSTQFTAAN        81    NaN        NaN   
...        ...           ...              ...       ...    ...        ...   
1137       NaN        D3ZH75  LPRPRLNTSDFQKLK       247   AKT1     P31749   
1138       NaN        P62755  AKRRRLSSLRASTSK       236   AKT1     P31749   
1139       NaN        D3ZBQ1  QSRPRSCTWPLQRPE        32   AKT1     P31749   
1140       NaN        P48679  RSRGRASSHSSQSQG       404   AKT1     P31749   
1141       NaN        P61016  RSAIRRASTIEMPQQ        16   AKT1     P31749   

     kinase_group kinase_family kinase_sub_family  binding_domain  \
0            CMGC          MAPK              ERK1             NaN   
1             AGC           PKA               NaN             NaN   
2            CMGC          MAPK              ERK1             NaN   
3              TK          INSR               NaN             NaN   
4             AGC           PKA               NaN             NaN   
...           ...           ...               ...             ...   
1137          AGC           AKT               NaN             NaN   
1138          AGC           AKT               NaN             NaN   
1139          AGC           AKT               NaN             NaN   
1140          AGC           AKT               NaN             NaN   
1141          AGC           AKT               NaN             NaN   

      taxonomy_id       species_name   db_source  SIGNOR_Score  \
0           10116  Rattus norvegicus  phosphoELM           NaN   
1           10116  Rattus norvegicus  phosphoELM           NaN   
2           10116  Rattus norvegicus  phosphoELM           NaN   
3           10116  Rattus norvegicus  phosphoELM           NaN   
4           10116  Rattus norvegicus  phosphoELM           NaN   
...           ...                ...         ...           ...   
1137        10116                NaN  KINASE-PSP           NaN   
1138        10116                NaN  KINASE-PSP           NaN   
1139        10116                NaN  KINASE-PSP           NaN   
1140        10116                NaN  KINASE-PSP           NaN   
1141        10116                NaN  KINASE-PSP           NaN   

                                          Full_Sequence  
0     MGDWSALGKLLDKVQAYSTAGGKVWLSVLFIFRILLLGTAVESAWG...  
1     MSMNKGPTLLDGDLPEQENVLQRVLQLPVVSGTCECFQKTYNSTKE...  
2     MGDWSALGKLLDKVQAYSTAGGKVWLSVLFIFRILLLGTAVESAWG...  
3     MASPPDTDGFSDVRKVGYLRKPKSMHKRFFVLRAASEAGGPARLEY...  
4     MSMNKGPTLLDGDLPEQENVLQRVLQLPVVSGTCECFQKTYNSTKE...  
...                                                 ...  
1137  MASGRPEELWEAVVGAAERFRARTGTELVLLTAAPPPPPRPGPCAY...  
1138  MKLNISFPATGCQKLIEVDDERKLRTFYEKRMATEVAADALGEEWK...  
1139  MAEAPASPVPLSPLEVELDPEFEPQSRPRSCTWPLQRPELQASPAK...  
1140  METPSQRRPTRSGAQASSTPLSPTRITRLQEKEDLQELNDRLAVYI...  
1141  MEKVQYLTRSAIRRASTIEMPQQARQNLQNLFINFCLILICLLLIC...  

[1107 rows x 15 columns]

In [7]:
dfloadkin=pd.read_csv("TreeData/HumanKinomeSeqFamilyClassification.csv",sep="\t")
kinaselist=dfloadkin["UniprotID"].to_list()

In [8]:
dfload=dfload[(~dfload["Kinase_Acc"].isna())&(dfload["Kinase_Acc"].isin(kinaselist))] #only keep entries where a kinase is known and has a human kinase accession

In [9]:
#takes a sequence and cuts it to a specified length around some position, if the sequence is too short it padds it with the <pad> token length must be an uneven number to ensure that left and right padding are the same length
def take_position(full_seq:str,position:int,length:int=21):
    if length%2==0: #make sure length is odd
        length+=1


    paddingtoken="<pad>"
    max_left=length//2
    max_right=length//2+1
    seq=""
    left, right = full_seq[:position], full_seq[position:]

    if len(left)<=max_left:
        to_pad=max_left-len(left)
        paddingl=paddingtoken*to_pad
        paddingl=paddingl+left
    
    else:
        paddingl=full_seq[position-max_left:position]

    if len(right)<max_right:
        
        to_pad=max_right-len(right)
        paddingr=paddingtoken*to_pad
        paddingr=right+paddingr
    
    else:
        paddingr=full_seq[position:position+max_right]


    
    seq=paddingl+seq+paddingr



    return seq

In [15]:
print(take_position("0123456789ABCDE",0,18))

<pad><pad><pad><pad><pad><pad><pad><pad><pad>0123456789


In [86]:
dfload['centered_sub_seq'] = dfload.apply(lambda row: take_position(row['Full_Sequence'], row['position'], length=1021), axis=1)
dfloadm['centered_sub_seq'] = dfloadm.apply(lambda row: take_position(row['Full_Sequence'], row['position'], length=1021), axis=1)
dfloadr['centered_sub_seq'] = dfloadr.apply(lambda row: take_position(row['Full_Sequence'], row['position'], length=1021), axis=1)

In [17]:
dfload[dfload.index==46463]

Substrate Substrate_Acc   Motif_Sequence  position Kinase Kinase_Acc  \
46463       NaN        O60841  QSFDDNDSEELEDKD       113  ACVR1     Q04771   

      kinase_group kinase_family kinase_sub_family  binding_domain  \
46463          TKL          STKR             STKR1             NaN   

       taxonomy_id species_name    db_source  SIGNOR_Score  \
46463         9606          NaN  KINASE-iKiP           NaN   

                                           Full_Sequence  \
46463  MGKKQKNKSEDSTKDDIDLDALAAEIEGAGAAKEQEPQKSKGKKKK...   

                                        centered_sub_seq  
46463  <pad><pad><pad><pad><pad><pad><pad><pad><pad><...

In [14]:
dfloadm.loc[dfloadm["Kinase"]=="PKCA","Kinase"]="PRKCA"
dfloadr.loc[dfloadr["Kinase"]=="PKCA","Kinase"]="PRKCA"

In [174]:
dfloadm.to_csv("deduplicated_mouse_fullSeq_centered.tsv",sep="\t",index=False)
dfloadr.to_csv("deduplicated_rat_fullSeq_centered.tsv",sep="\t",index=False)

In [236]:
dfload.to_csv("deduplicated_human_fullSeq_centered.tsv",sep="\t",index=False)

In [18]:
dfload=pd.read_csv("deduplicated_human_fullSeq_centered.tsv",sep="\t")

/tmp/ipykernel_18946/690255022.py:1: DtypeWarning: Columns (0,11) have mixed types. Specify dtype option on import or set low_memory=False.
  dfload=pd.read_csv("deduplicated_human_fullSeq_centered.tsv",sep="\t")


In [ ]:
#try to deal with mouse and rat kinases

In [11]:
dfloadm["Kinase"].value_counts()

Kinase
MAPK1       168
PRKACA      152
MTOR         75
SRC          74
CSNK2A1      65
           ... 
TSSK3         1
FLT3          1
PCTAIRE1      1
PAK1          1
TYK2          1
Name: count, Length: 145, dtype: int64

In [12]:
# a lot of entries are just random small peptides that are weirdly short/barely annotated in uniprot, i think ill take the few that 
unique_mouse_kinases=dfloadm["Kinase"].value_counts()[dfloadm["Kinase"].value_counts()>=15].index

In [13]:
dfloadm["Kinase"].value_counts()[dfloadm["Kinase"].value_counts()>=15]

Kinase
MAPK1       168
PRKACA      152
MTOR         75
SRC          74
CSNK2A1      65
CDK5         56
GSK3B        51
PRKCA        48
CSNK1D       48
MAPK14       48
MAPK3        44
FYN          42
CAMK2A       38
PRKAA1       35
CDK1         29
AKT1         28
MAPK8        25
CDK2         25
LYN          25
LCK          21
MAPKAPK2     21
JAK2         19
SYK          16
ADRBK1       16
ABL1         16
AURKB        15
EGFR         15
PKCA         15
Name: count, dtype: int64

In [168]:
mkin=pd.DataFrame(unique_mouse_kinases,columns=["Kinase"])

In [ ]:
#mkin.to_csv("mkfull.txt",sep=",")

In [134]:
mousemapping=pd.read_csv("TreeData/mousekinase_mapping.tsv",sep="\t")

In [159]:
merged=pd.merge(mkin,mousemapping,left_on="Kinase",right_on="From",how="inner")

In [160]:
merged

Kinase      From   Entry  Reviewed   Entry Name  \
0      MAPK1     MAPK1  P63085  reviewed   MK01_MOUSE   
1     PRKACA    PRKACA  P05132  reviewed  KAPCA_MOUSE   
2       MTOR      MTOR  Q9JLN9  reviewed   MTOR_MOUSE   
3        SRC       SRC  P05480  reviewed    SRC_MOUSE   
4    CSNK2A1   CSNK2A1  Q60737  reviewed  CSK21_MOUSE   
5       CDK5      CDK5  P49615  reviewed   CDK5_MOUSE   
6      GSK3B     GSK3B  Q9WV60  reviewed  GSK3B_MOUSE   
7      PRKCA     PRKCA  P20444  reviewed   KPCA_MOUSE   
8     CSNK1D    CSNK1D  Q9DC28  reviewed   KC1D_MOUSE   
9     MAPK14    MAPK14  P47811  reviewed   MK14_MOUSE   
10     MAPK3     MAPK3  Q63844  reviewed   MK03_MOUSE   
11       FYN       FYN  P39688  reviewed    FYN_MOUSE   
12    CAMK2A    CAMK2A  P11798  reviewed  KCC2A_MOUSE   
13    PRKAA1    PRKAA1  Q5EG47  reviewed  AAPK1_MOUSE   
14      CDK1      CDK1  P11440  reviewed   CDK1_MOUSE   
15      AKT1      AKT1  P31750  reviewed   AKT1_MOUSE   
16     MAPK8     MAPK8  Q91Y86  reviewed   MK08_MOUSE   
17      CDK2      CDK2  P97377  reviewed   CDK2_MOUSE   
18       LYN       LYN  P25911  reviewed    LYN_MOUSE   
19       LCK       LCK  P06240  reviewed    LCK_MOUSE   
20  MAPKAPK2  MAPKAPK2  P49138  reviewed  MAPK2_MOUSE   
21      JAK2      JAK2  Q62120  reviewed   JAK2_MOUSE   
22       SYK       SYK  P48025  reviewed   KSYK_MOUSE   
23    ADRBK1    ADRBK1  Q99MK8  reviewed  ARBK1_MOUSE   
24      ABL1      ABL1  P00520  reviewed   ABL1_MOUSE   
25     AURKB     AURKB  O70126  reviewed  AURKB_MOUSE   
26      EGFR      EGFR  Q01279  reviewed   EGFR_MOUSE   

                                        Protein names  \
0   Mitogen-activated protein kinase 1 (MAP kinase...   
1   cAMP-dependent protein kinase catalytic subuni...   
2   Serine/threonine-protein kinase mTOR (EC 2.7.1...   
3   Proto-oncogene tyrosine-protein kinase Src (EC...   
4   Casein kinase II subunit alpha (CK II alpha) (...   
5   Cyclin-dependent kinase 5 (EC 2.7.11.1) (Cell ...   
6   Glycogen synthase kinase-3 beta (GSK-3 beta) (...   
7   Protein kinase C alpha type (PKC-A) (PKC-alpha...   
8   Casein kinase I isoform delta (CKI-delta) (CKI...   
9   Mitogen-activated protein kinase 14 (MAP kinas...   
10  Mitogen-activated protein kinase 3 (MAP kinase...   
11  Tyrosine-protein kinase Fyn (EC 2.7.10.2) (Pro...   
12  Calcium/calmodulin-dependent protein kinase ty...   
13  5'-AMP-activated protein kinase catalytic subu...   
14  Cyclin-dependent kinase 1 (CDK1) (EC 2.7.11.22...   
15  RAC-alpha serine/threonine-protein kinase (EC ...   
16  Mitogen-activated protein kinase 8 (MAP kinase...   
17  Cyclin-dependent kinase 2 (EC 2.7.11.22) (Cell...   
18  Tyrosine-protein kinase Lyn (EC 2.7.10.2) (V-y...   
19  Proto-oncogene tyrosine-protein kinase LCK (EC...   
20  MAP kinase-activated protein kinase 2 (MAPK-ac...   
21  Tyrosine-protein kinase JAK2 (EC 2.7.10.2) (Ja...   
22  Tyrosine-protein kinase SYK (EC 2.7.10.2) (Spl...   
23  Beta-adrenergic receptor kinase 1 (Beta-ARK-1)...   
24  Tyrosine-protein kinase ABL1 (EC 2.7.10.2) (Ab...   
25  Aurora kinase B (EC 2.7.11.1) (Aurora 1) (Auro...   
26     Epidermal growth factor receptor (EC 2.7.10.1)   

                                    Gene Names              Organism  \
0                        Mapk1 Erk2 Mapk Prkm1  Mus musculus (Mouse)   
1                                 Prkaca Pkaca  Mus musculus (Mouse)   
2                              Mtor Frap Frap1  Mus musculus (Mouse)   
3                                          Src  Mus musculus (Mouse)   
4                                Csnk2a1 Ckiia  Mus musculus (Mouse)   
5                      Cdk5 Cdkn5 Crk6 PSSALRE  Mus musculus (Mouse)   
6                                        Gsk3b  Mus musculus (Mouse)   
7                                   Prkca Pkca  Mus musculus (Mouse)   
8                                 Csnk1d Hckid  Mus musculus (Mouse)   
9                      Mapk14 Crk1 Csbp1 Csbp2  Mus musculus (Mouse)   
10                  

In [163]:
dfloadr["Kinase"].value_counts()

Kinase
PRKACA     125
PRKCA       95
MAPK1       81
CAMK2A      71
CAMK2B      51
          ... 
CAMK4        1
ABL2         1
RPS6KA2      1
DAPK1        1
PKCA         1
Name: count, Length: 66, dtype: int64

In [164]:
unique_rat_kinases=dfloadr["Kinase"].value_counts()[dfloadr["Kinase"].value_counts()>=15].index

In [167]:
unique_rat_kinases
rkin=pd.DataFrame(unique_rat_kinases,columns=["Kinase"])

In [ ]:
#rkin.to_csv("rkfull.txt",sep=",")

In [170]:
ratmapping=pd.read_csv("TreeData/ratkinase_mapping.tsv",sep="\t")

In [171]:
rmerged=pd.merge(rkin,ratmapping,left_on="Kinase",right_on="From",how="inner")

In [ ]:
##trim human kinases to domain

In [19]:
dfloadkin

Unnamed: 0     xName Manning Name  HGNC Name   \
0             0     AAK1          AAK1       AAK1    
1             1     ABL1           ABL       ABL1    
2             2     ABL2           ARG       ABL2    
3             3      ABR           ABR        ABR    
4             4      ACK           ACK       TNK2    
..          ...       ...           ...        ...   
531         531     p38g          p38g     MAPK12    
532         532   p70S6K        p70S6K    RPS6KB1    
533         533  p70S6Kb       p70S6Kb    RPS6KB2    
534         534   skMLCK        skMLCK      MYLK2    
535         535   smMLCK        smMLCK       MYLK    

                                          Kinase Name      Group  Family   \
0                     AP2-associated protein kinase 1      Other     NAK    
1                        Tyrosine-protein kinase ABL1         TK     Abl    
2                   Abelson tyrosine-protein kinase 2         TK     Abl    
3    Active breakpoint cluster region-related protein   Atypical     BCR    
4                            Activated CDC42 kinase 1         TK     Ack    
..                                                 ...        ...     ...   
531               Mitogen-activated protein kinase 12       CMGC    MAPK    
532                Ribosomal protein S6 kinase beta-1        AGC     RSK    
533                Ribosomal protein S6 kinase beta-2        AGC     RSK    
534                       Myosin light chain kinase 2       CAMK    MLCK    
535                         Myosin light chain kinase       CAMK    MLCK    

    SubFamily  UniprotID                                    Kinase_Sequence  
0          NaN    Q2M2I8  MKKFFDSRREQGGSGLGSGSSGGGGSTSGLGSGYIGRVFGIGRQQV...  
1          NaN    P00519  MLEICLKLVGCKSKKGLSSSSSCYLEEALQRPVASDFEPQGLSEAA...  
2          NaN    P42684  MGQQVGRVGEAPGLQQPQPRGIRGSSAARPSGRRRDPAGRTTETGF...  
3          NaN    Q12979  MEPLSHRGLPRLSWIDTLYSNFSYGTDEYDGEGNEEQKGPPEGSET...  
4          NaN    Q07912  MQPEEGTGWLLELLSEVQLQQYFLRLRDDLNVTRLSHFEYVKNEDL...  
..         ...       ...                                                ...  
531       p38     P53778  MSSPPPARSGFYRQEVTKTAWEVRAVYRDLQPVGSGAYGAVCSAVD...  
532    RSKp70     P23443  MRRRRRRDGFYPAPDFRDREAEDMAGVFDIDLDQPEDAGSEDELEE...  
533    RSKp70     Q9UBS0  MAAVFDLDLETEEGSEGEGEPELSPADACPLAELRAAGLEPVGHYE...  
534        NaN    Q9H1R3  MATENGAVELGIQNPSTDKAPKGPTGERPLAAGKDPGPPDPKKAPD...  
535        NaN    Q15746  MGDVKLVASSHISKTSLSVDPSRVDSMPLTEAPAFILPPRNLCIKE...  

[536 rows x 10 columns]

In [20]:
dfall3=pd.read_csv("masterDatabaseall3.tsv",sep="\t") #dataframe to check if a kinase actually has examples

In [175]:
import requests

def get_protein_kinase_domains(uniprot_id):
    url = f"https://rest.uniprot.org/uniprotkb/{uniprot_id}.json"
    response = requests.get(url)
    data = response.json()

    kinase_domains = []
    for feature in data.get("features", []):
        if feature.get("type") == "Domain" and "protein kinase" in feature.get("description", "").lower():
            location = feature.get("location", {})
            start = location.get("start", {}).get("value")
            end = location.get("end", {}).get("value")
            kinase_domains.append((start, end))

    return kinase_domains

# Example use
print(get_protein_kinase_domains("Q8WZ42"))

[(32178, 32432)]


In [178]:
#center mouse and rat kinases to domain
mdomainlistlist=[]
rdomainlistlist=[]
for kinase in merged["Entry"]:
    kinasedomains=get_protein_kinase_domains(kinase)
    mdomainlistlist+=[kinasedomains]


for kinase in rmerged["Entry"]:
    kinasedomains=get_protein_kinase_domains(kinase)
    rdomainlistlist+=[kinasedomains]

In [ ]:
mdomainlistlist[2]=[(1982,2517)] #mtor kinase is atypical, manually added the Fat FATc region

In [185]:
mdomaincenters=mdomainlistlist.copy()
for i,values in enumerate(mdomainlistlist):
    if len(values)>1:
        mdomaincenters[i]=(values[0][1]+values[1][0])//2
    else:
        mdomaincenters[i]=(values[0][0]+values[0][1])//2

In [188]:
rdomaincenters=rdomainlistlist.copy()
for i,values in enumerate(rdomainlistlist):
    if len(values)>1:
        rdomaincenters[i]=(values[0][1]+values[1][0])//2
    else:
        rdomaincenters[i]=(values[0][0]+values[0][1])//2

In [189]:
rdomaincenters

[171, 468, 167, 142, 143, 187, 181, 145, 396, 198, 279, 153, 145, 1161, 394]

In [192]:
merged["Domaincenters"]=mdomaincenters
rmerged["Domaincenters"]=rdomaincenters

In [193]:
merged["Centered_Kinase_Sequence"]=merged.apply(lambda row: take_position(row['Sequence'], row['Domaincenters'], length=1021), axis=1)
rmerged["Centered_Kinase_Sequence"]=rmerged.apply(lambda row: take_position(row['Sequence'], row['Domaincenters'], length=1021), axis=1)


In [195]:
merged.to_csv("TreeData/MouseKinomeSeqFamilyClassification_centered_15substrates.csv",index=False)
rmerged.to_csv("TreeData/RatKinomeSeqFamilyClassification_centered_15substrates.csv",index=False)


In [22]:
domainlistlist=[]
for kinase in kinaselist:
    kinasedomains=get_protein_kinase_domains(kinase)
    domainlistlist+=[kinasedomains]

In [23]:
domainlistlist

[[(46, 315)],
 [(242, 493)],
 [(288, 539)],
 [],
 [(126, 385)],
 [(192, 485)],
 [(190, 480)],
 [(155, 467)],
 [(200, 618)],
 [(329, 518)],
 [(191, 423)],
 [(179, 419)],
 [(150, 408)],
 [(152, 409)],
 [(148, 405)],
 [(1116, 1392)],
 [(202, 492)],
 [(208, 502)],
 [(207, 497)],
 [(195, 485)],
 [(27, 279)],
 [(16, 268)],
 [(22, 286)],
 [(528, 805)],
 [(513, 786)],
 [(310, 570)],
 [],
 [],
 [(536, 807)],
 [(1390, 1625)],
 [(1901, 2133)],
 [(1017, 1237)],
 [(133, 383)],
 [(77, 327)],
 [(43, 293)],
 [(191, 453)],
 [(191, 453)],
 [],
 [],
 [],
 [],
 [(51, 316)],
 [(241, 494)],
 [],
 [(234, 525)],
 [(204, 494)],
 [(203, 504)],
 [(417, 675)],
 [(457, 717)],
 [],
 [],
 [],
 [],
 [(191, 445)],
 [(34, 285)],
 [(19, 270)],
 [(402, 655)],
 [(787, 1085)],
 [(766, 1050)],
 [(12, 276)],
 [(796, 1066)],
 [(4, 288)],
 [(4, 287)],
 [(58, 574)],
 [(39, 323)],
 [(21, 335)],
 [(4, 286)],
 [(4, 286)],
 [(6, 295)],
 [(4, 286)],
 [(13, 300)],
 [(12, 295)],
 [(21, 335)],
 [(19, 315)],
 [(4, 287)],
 [(4, 287)],
 [

In [24]:
emptylist=[] # how many of my kinases have no kinase domains
for i,kinasedomains in enumerate(domainlistlist):
    if (kinasedomains == []):
        emptylist+=[kinaselist[i]]
print(len(emptylist))

30


In [25]:
for i,kinasedomains in enumerate(domainlistlist): #which of these do still have data entries for phosphorylation
    if (kinasedomains == []):
        if len(dfload[dfload["Kinase_Acc"]==kinaselist[i]]) != 0:
            print("Warning", kinaselist[i], "has no kinase domain but",len(dfload[dfload["Kinase_Acc"]==kinaselist[i]]),"entries¦ entry:",i)


Warning Q13315 has no kinase domain but 388 entries¦ entry: 26
Warning Q13535 has no kinase domain but 141 entries¦ entry: 27
Warning Q9UIG0 has no kinase domain but 1 entries¦ entry: 38
Warning O14874 has no kinase domain but 1 entries¦ entry: 39
Warning P53004 has no kinase domain but 1 entries¦ entry: 43
Warning O60885 has no kinase domain but 19 entries¦ entry: 51
Warning P78527 has no kinase domain but 162 entries¦ entry: 129
Warning P42345 has no kinase domain but 170 entries¦ entry: 174
Warning Q6IBK5 has no kinase domain but 2 entries¦ entry: 189
Warning Q15118 has no kinase domain but 36 entries¦ entry: 344
Warning Q15119 has no kinase domain but 8 entries¦ entry: 345
Warning Q15120 has no kinase domain but 2 entries¦ entry: 346
Warning Q16654 has no kinase domain but 6 entries¦ entry: 347
Warning Q96Q15 has no kinase domain but 10 entries¦ entry: 430


In [ ]:
# Q13315 -ATM kinase wikipedia: HEAT repeat domain -> FRAP-ATM-TRAP (FAT) domain -> Kinase domain ->PIKK regulatory domain -> FATC domain
# FAT ends at 2566, FATC starts at 3024 take sequence between the loop - uniprot annotated as  PI3K catalytic, G-loop, Catalytic loop, Activation loop
# Q13535 -ATR same as ATM; also has FAT into PI3K catalytic, G-loop, Catalytic loop, Activation loop into FATC
# FAT ends at 2185, FATC starts at 2612
# Q9UIG0 -BAZ1B tyrosine kinase WAC domain, DDT domain, some coils, Bromo domain, no indication of kinase?
# O14874 -BCKD is a histidine kinase
# hist kinase (159,404)
# P53004 only sequence conflicts annotated toss
# O60885 -BRD4 not clear where kinase domain is... but the thing is only 1339 AA long and 1116-1339 is disordered, and first 58 AA are disordered
# take (58,1079) maybe
# P78527 -DNA dependent protein kinase catalytic subunit,same deal as atm and atr with FAT and FATC and catalytic loops
# FAT ends at 3539, FATC starts at 4096
# P42345 -mTOR same sotry as atm/atr
# FAT ends at 1982, FATC starts at 2517
# Q6IBK5 -no mention of kinaseactivity?? ~
# Q15118 .histidine kinase
# hist kinase (163,393)
# Q15119 .histidine kinase
# hist kinase (135,364)
# Q15120 .histidine kinase
# hist kinase (131,362)
# Q16654 .histidine kinase
# hist kinase (138,368)
# Q96Q15 same pattern as atm with  FAt - FATC but FAT and FATC are too far away to encode that part entirely
# PI3K catalytic start at 2124 PI3K catalytic end at 2463

In [26]:
#add the domains for kinases with more than 30 entries from comment above
domainlistlist[26]=[(2566,3024)] #ATM
domainlistlist[27]=[(2185,2612)] #ATR
domainlistlist[129]=[(3539,4096)] #PRKDC
domainlistlist[174]=[(1982,2517)] #mTOR
domainlistlist[344]=[(163,393)] #PDK1

In [27]:
domainlistlist

[[(46, 315)],
 [(242, 493)],
 [(288, 539)],
 [],
 [(126, 385)],
 [(192, 485)],
 [(190, 480)],
 [(155, 467)],
 [(200, 618)],
 [(329, 518)],
 [(191, 423)],
 [(179, 419)],
 [(150, 408)],
 [(152, 409)],
 [(148, 405)],
 [(1116, 1392)],
 [(202, 492)],
 [(208, 502)],
 [(207, 497)],
 [(195, 485)],
 [(27, 279)],
 [(16, 268)],
 [(22, 286)],
 [(528, 805)],
 [(513, 786)],
 [(310, 570)],
 [(2566, 3024)],
 [(2185, 2612)],
 [(536, 807)],
 [(1390, 1625)],
 [(1901, 2133)],
 [(1017, 1237)],
 [(133, 383)],
 [(77, 327)],
 [(43, 293)],
 [(191, 453)],
 [(191, 453)],
 [],
 [],
 [],
 [],
 [(51, 316)],
 [(241, 494)],
 [],
 [(234, 525)],
 [(204, 494)],
 [(203, 504)],
 [(417, 675)],
 [(457, 717)],
 [],
 [],
 [],
 [],
 [(191, 445)],
 [(34, 285)],
 [(19, 270)],
 [(402, 655)],
 [(787, 1085)],
 [(766, 1050)],
 [(12, 276)],
 [(796, 1066)],
 [(4, 288)],
 [(4, 287)],
 [(58, 574)],
 [(39, 323)],
 [(21, 335)],
 [(4, 286)],
 [(4, 286)],
 [(6, 295)],
 [(4, 286)],
 [(13, 300)],
 [(12, 295)],
 [(21, 335)],
 [(19, 315)],
 [(4

In [28]:
for i,domains in enumerate(domainlistlist): #get problematic kinases that have more than 1 proteinkinase domain that spans more than 1021 AA
    if domains!= []:
        if domains[len(domains)-1][1]-domains[0][0]>1021:
            print(domains)
            print("Warning", kinaselist[i], "has domains too far apart with",len(dfload[dfload["Kinase_Acc"]==kinaselist[i]]),"entries¦ entry:",i)


[(6468, 6721), (7672, 7924)]
Warning Q5VST9 has domains too far apart with 0 entries¦ entry: 328
[(6468, 6721), (7672, 7924)]
Warning Q5VST9 has domains too far apart with 0 entries¦ entry: 329
[(1601, 1854), (2966, 3218)]
Warning Q15772 has domains too far apart with 0 entries¦ entry: 432
[(1601, 1854), (2966, 3218)]
Warning Q15772 has domains too far apart with 0 entries¦ entry: 433
[(1, 435), (1446, 1893)]
Warning P21675 has domains too far apart with 4 entries¦ entry: 461


In [29]:
for i,domains in enumerate(domainlistlist): #get problematic kinases that have more than 1 proteinkinase domain
    if len(domains)>1:
        name=dfloadkin["HGNC Name "][dfloadkin["UniprotID"]==kinaselist[i]].iloc[0]
        print("Warning", name, "has more than one domain with ",len(dfload[dfload["Kinase_Acc"]==kinaselist[i]]),"entries¦ entry",i)
        

#reason why they appear double is that the familyclassification file im using lists domains and not whole kinases (as in 2 entries with the accession Q9p2K8, one for each kinase domain )

Warning EIF2AK4  has more than one domain with  16 entries¦ entry 181
Warning EIF2AK4  has more than one domain with  16 entries¦ entry 182
Warning JAK1  has more than one domain with  24 entries¦ entry 217
Warning JAK1  has more than one domain with  24 entries¦ entry 218
Warning JAK2  has more than one domain with  156 entries¦ entry 219
Warning JAK2  has more than one domain with  156 entries¦ entry 220
Warning JAK3  has more than one domain with  138 entries¦ entry 221
Warning JAK3  has more than one domain with  138 entries¦ entry 222
Warning RPS6KA5  has more than one domain with  235 entries¦ entry 293
Warning RPS6KA5  has more than one domain with  235 entries¦ entry 294
Warning RPS6KA4  has more than one domain with  72 entries¦ entry 295
Warning RPS6KA4  has more than one domain with  72 entries¦ entry 296
Warning OBSCN  has more than one domain with  0 entries¦ entry 328
Warning OBSCN  has more than one domain with  0 entries¦ entry 329
Warning RPS6KA1  has more than one dom

In [35]:
domainlistlist[181]

[(296, 539), (590, 1001)]

In [30]:
domainlist=domainlistlist.copy()
for i,domains in enumerate(domainlistlist): #get problematic kinases that have more than 1 proteinkinase domain
    if len(domains)>1:
        domainlist[i]=[(domains[0][0],domains[1][1])]



In [37]:
domainlist[182]

[(296, 1001)]

In [31]:
#remove kinases with less than 20 entries
indexes_to_keep=[False for idx in range(len(domainlistlist))]
for i,domains in enumerate(domainlistlist): #get problematic kinases that have more than 1 proteinkinase domain
    if len(dfload[dfload["Kinase_Acc"]==kinaselist[i]])>20:
        indexes_to_keep[i]=True

sum([int(i)for i in indexes_to_keep])

311

In [32]:
#remove duplicated kinases
unique=[True for idx in range(len(domainlistlist))]
seen=[]
for i,acc in enumerate(kinaselist):
    if acc in seen:
        unique[i]=False
    seen+=[acc]

indexes_to_keep=[i&j for i,j in zip(indexes_to_keep,unique)]
sum([int(i)for i in indexes_to_keep])

301

In [33]:
domaincenters=domainlist.copy()
for i,values in enumerate(domainlist):
    if values != []:
        domaincenters[i]=(values[0][0]+values[0][1])//2

In [34]:
dfloadkin["Domain"]=domainlist
dfloadkin["Domaincenters"]=domaincenters

In [35]:
dfloadkin[indexes_to_keep][dfloadkin["HGNC Name "]=="PRKDC "]

/tmp/ipykernel_18946/3027003812.py:1: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  dfloadkin[indexes_to_keep][dfloadkin["HGNC Name "]=="PRKDC "]


Unnamed: 0   xName Manning Name  HGNC Name   \
129         129  DNAPK         DNAPK      PRKDC    

                                        Kinase Name      Group  Family   \
129  DNA-dependent protein kinase catalytic subunit   Atypical    PIKK    

    SubFamily  UniprotID                                    Kinase_Sequence  \
129     DNAPK     P78527  MAGSGAGVRCSLLRLQETLSAADRCGAALAGHQLIRGLGQECVLSS...   

             Domain Domaincenters  
129  [(3539, 4096)]          3817

In [36]:
dfkin80plus=dfloadkin[indexes_to_keep].copy()
dfkin80plus["Centered_Kinase_Sequence"]=dfkin80plus.apply(lambda row: take_position(row['Kinase_Sequence'], row['Domaincenters'], length=1021), axis=1)

In [37]:
dfkin80plus.to_csv("TreeData/HumanKinomeSeqFamilyClassification_centered_20substrates.csv",index=False) #contains kinases and their kinase domains with a 1021 window

In [38]:

dfkin80plus

Unnamed: 0     xName Manning Name  HGNC Name   \
1             1     ABL1           ABL       ABL1    
2             2     ABL2           ARG       ABL2    
4             4      ACK           ACK       TNK2    
5             5    ACTR2         ACTR2     ACVR2A    
12           12     AKT1          AKT1       AKT1    
..          ...       ...           ...        ...   
530         530     p38d          p38d     MAPK13    
531         531     p38g          p38g     MAPK12    
532         532   p70S6K        p70S6K    RPS6KB1    
533         533  p70S6Kb       p70S6Kb    RPS6KB2    
534         534   skMLCK        skMLCK      MYLK2    

                                   Kinase Name  Group  Family  SubFamily   \
1                 Tyrosine-protein kinase ABL1     TK     Abl         NaN   
2            Abelson tyrosine-protein kinase 2     TK     Abl         NaN   
4                     Activated CDC42 kinase 1     TK     Ack         NaN   
5                     Activin receptor type-2A    TKL    STKR      STKR2    
12   RAC-alpha serine/threonine-protein kinase    AGC     Akt         NaN   
..                                          ...    ...     ...        ...   
530        Mitogen-activated protein kinase 13   CMGC    MAPK        p38    
531        Mitogen-activated protein kinase 12   CMGC    MAPK        p38    
532         Ribosomal protein S6 kinase beta-1    AGC     RSK     RSKp70    
533         Ribosomal protein S6 kinase beta-2    AGC     RSK     RSKp70    
534                Myosin light chain kinase 2   CAMK    MLCK         NaN   

    UniprotID                                    Kinase_Sequence  \
1      P00519  MLEICLKLVGCKSKKGLSSSSSCYLEEALQRPVASDFEPQGLSEAA...   
2      P42684  MGQQVGRVGEAPGLQQPQPRGIRGSSAARPSGRRRDPAGRTTETGF...   
4      Q07912  MQPEEGTGWLLELLSEVQLQQYFLRLRDDLNVTRLSHFEYVKNEDL...   
5      P27037  MGAAAKLAFAVFLISCSSGAILGRSETQECLFFNANWEKDRTNQTG...   
12     P31749  MSDVAIVKEGWLHKRGEYIKTWRPRYFLLKNDGTFIGYKERPQDVD...   
..        ...                                                ...   
530    O15264  MSLIRKKGFYKQDVNKTAWELPKTYVSPTHVGSGAYGSVCSAIDKR...   
531    P53778  MSSPPPARSGFYRQEVTKTAWEVRAVYRDLQPVGSGAYGAVCSAVD...   
532    P23443  MRRRRRRDGFYPAPDFRDREAEDMAGVFDIDLDQPEDAGSEDELEE...   
533    Q9UBS0  MAAVFDLDLETEEGSEGEGEPELSPADACPLAELRAAGLEPVGHYE...   
534    Q9H1R3  MATENGAVELGIQNPSTDKAPKGPTGERPLAAGKDPGPPDPKKAPD...   

           Domain Domaincenters  \
1    [(242, 493)]           367   
2    [(288, 539)]           413   
4    [(126, 385)]           255   
5    [(192, 485)]           338   
12   [(150, 408)]           279   
..            ...           ...   
530   [(25, 308)]           166   
531   [(27, 311)]           169   
532   [(91, 352)]           221   
533   [(67, 328)]           197   
534  [(285, 540)]           412   

                              Centered_Kinase_Sequence  
1    <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
2    <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
4    <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
5    <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
12   <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
..                                                 ...  
530  <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
531  <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
532  <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
533  <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
534  <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  

[301 rows x 13 columns]

In [148]:
dfload

Substrate Substrate_Acc   Motif_Sequence  position  Kinase Kinase_Acc  \
0           NaN        P06241  TDPTPQHYPSFGVTS        39     FYN     P06241   
1           NaN        P05412  VPEMPGETPPLSPID       239   GSK3A     P49840   
3           NaN        P06213  SLGFKRSYEEHIPYT      1355    INSR     P06213   
4           NaN        P06730  DTATKSGSTTKNRFV       209    MNK1     Q9BUB5   
5           NaN        P45983  AGTSFMMTPYVVTRY       183  MAP2K7     O14733   
...         ...           ...              ...       ...     ...        ...   
46463       NaN      Q92734-2  YTQPGPGYR______       395    ABL2     P42684   
46464       NaN      Q96HC4-7  VERYTEFYHVPTHSD       148    ABL2     P42684   
46465       NaN        Q9BTC0  KALGSAQYEDPRNLH      1700    ABL2     P42684   
46466       NaN        Q9H3P7  RDCHEEVYAGSHQYP       492    ABL2     P42684   
46467       NaN        Q9NUQ9  TESEKEIYNQVNVVL        36    ABL2     P42684   

      kinase_group kinase_family kinase_sub_family  binding_domain  \
0               TK           SRC               NaN             NaN   
1             CMGC           GSK               NaN             NaN   
3               TK          INSR               NaN             NaN   
4             CAMK       MAPKAPK               MNK             NaN   
5              STE          STE7               NaN             NaN   
...            ...           ...               ...             ...   
46463           TK           ABL               NaN             NaN   
46464           TK           ABL               NaN             NaN   
46465           TK           ABL               NaN             NaN   
46466           TK           ABL               NaN             NaN   
46467           TK           ABL               NaN             NaN   

       taxonomy_id  species_name    db_source  SIGNOR_Score  \
0             9606  Homo sapiens   phosphoELM           NaN   
1             9606  Homo sapiens   phosphoELM           NaN   
3             9606  Homo sapiens   phosphoELM           NaN   
4             9606  Homo sapiens   phosphoELM           NaN   
5             9606  Homo sapiens   phosphoELM           NaN   
...            ...           ...          ...           ...   
46463         9606           NaN  KINASE-iKiP           NaN   
46464         9606           NaN  KINASE-iKiP           NaN   
46465         9606           NaN  KINASE-iKiP           NaN   
46466         9606           NaN  KINASE-iKiP           NaN   
46467         9606           NaN  KINASE-iKiP           NaN   

                                           Full_Sequence  \
0      MGCVQCKDKEATKLTEERDGSLNQSSGYRYGTDPTPQHYPSFGVTS...   
1      MTAKMETTFYDDALNASFLPSESGPYGYSNPKILKQSMTLNLADPV...   
3      MATGGRRGAAAAPLLVAVAALLLGAAGHLYPGEVCPGMDIRNNLTR...   
4      MATVEPETTPTPNPPTTEEEKTESNQEVANPEHYIKHPLQNRWALW...   
5      MSRSKRDNNFYSVEIGDSTFTVLKRYQNLKPIGSGAQGIVCAAYDA...   
...                                                  ...   
46463  MNGQLDLSGKLIIKAQLGEDIRRIPIHNEDITYDELVLMMQRVFRG...   
46464  MSNYSVSLVGPAPWGFRLQGGKDFNMPLTISSLKDGGKAAQANVRI...   
46465  MDDKGDPSNEEAPKAIKPTSKEFRKTWGFRRTTIAKREGAGDAEAD...   
46466  MAAVLNAERLEVSVDGLTLSPDPEERPGAEGAPLLPPPLPPPSPPG...   
46467  MGNLLKVLTCTDLEQGPNFFLDFENAQPTESEKEIYNQVNVVLKDA...   

                                        centered_sub_seq  
0      <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
1      <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
3      TSSGTGAEDPRPSRKRRSLGDVGNVTVAVPTVAAFPNTSSTSVPTS...  
4      <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
5      <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
...                                                  ...  
46463  <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
46464  <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
46465  IHIGGRIAPKTVWDYVGKLKSSVSKELCLIRFHPATEEEEVAYISL...  
46466  <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
46467  <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  

[45540 rows x 16 columns]

In [147]:
len(dfload["centered_sub_seq"].unique())

19156

## Start of ESM2

In [196]:
import torch
import esm

In [95]:
proteinlintuples=dfload.apply(lambda row: (row["Substrate_Acc"],row["position"],row["centered_seq"]),axis=1).to_list() #proteintuples is a list containing tuples of (Substrate, position ,centered sequence)
proteindata=dfload.apply(lambda row: (row["Substrate_Acc"],row["centered_seq"]),axis=1).to_list() 

In [96]:
proteindata[:10]

[('P06241',
  '<pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad>

In [70]:
model_name = "esm2_t12_35M_UR50D"
model, alphabet = esm.pretrained.load_model_and_alphabet(model_name)

In [ ]:
batch_converter = alphabet.get_batch_converter()

# Prepare data for the batch converter (labels, sequences, and then get tokens)
batch_labels, batch_strs, batch_tokens = batch_converter(proteindata[:100])

# Move tokens to the same device as the model


print(f"Batch tokens shape: {batch_tokens.shape}")



Batch tokens shape: torch.Size([100, 8193])


In [81]:
alphabet.all_toks

['<cls>',
 '<pad>',
 '<eos>',
 '<unk>',
 'L',
 'A',
 'G',
 'V',
 'S',
 'E',
 'R',
 'T',
 'I',
 'D',
 'P',
 'K',
 'Q',
 'N',
 'F',
 'Y',
 'M',
 'H',
 'W',
 'C',
 'X',
 'B',
 'U',
 'Z',
 'O',
 '.',
 '-',
 '<null_1>',
 '<mask>']

In [80]:
batch_tokens

tensor([[0, 1, 1,  ..., 1, 1, 2],
        [0, 1, 1,  ..., 1, 1, 2],
        [0, 1, 1,  ..., 1, 1, 2],
        ...,
        [0, 1, 1,  ..., 1, 1, 2],
        [0, 1, 1,  ..., 1, 1, 2],
        [0, 1, 1,  ..., 1, 1, 2]])

In [43]:
from transformers import AutoTokenizer, EsmModel

2025-05-14 12:53:23.337910: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1747220003.354784    7617 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1747220003.359748    7617 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


In [44]:
model_src="ESM-2/esm2_t12_35M_UR50D/"
tokenizer = AutoTokenizer.from_pretrained(model_src)

model = EsmModel.from_pretrained(model_src)

Some weights of EsmModel were not initialized from the model checkpoint at ESM-2/esm2_t12_35M_UR50D/ and are newly initialized: ['esm.pooler.dense.bias', 'esm.pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [66]:

inputs = tokenizer(["<pad><eos>HHH<pad>"], return_tensors="pt")
inputs

{'input_ids': tensor([[ 0,  1,  2, 21, 21, 21,  1,  2]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1]])}

In [76]:
with torch.no_grad():
    # Forward pass, get hidden states
    outputs = model(**inputs)

In [77]:
outputs[0].shape  # (batch_size, sequence_length, hidden_size)

torch.Size([1, 8, 480])

In [85]:
tokenizer.encode("<pad><mask><eos>TT")

[0, 1, 32, 2, 11, 11, 2]

In [247]:
dfload[dfload["centered_sub_seq"]=='ENILLSVNEQYIRRLAAEATEWQRSGAPPPSGSAVSTAPQPKPADKMSKNKKKKLKKKQKRQAELLEKRMQEIEEMEKESGPGQKRPNKQEESESPVERPLKENPPNKMTQEKLEESSTIGQDQTLMERDTEGGAAEINCNGVIEVINYTQNSNNETLRHKEDLHNANDCDVQNLNQESSFLSSQNGDSSTSQETDSCTPITSEVSDTMVCQSSSTVGQSFSEQHISQLQESIRAEIPCEDEQEQEHNGPLDNKGKSTAGNFLVNPLEPKNAEKLKVKIADLGNACWVHKHFTEDIQTRQYRSLEVLIGSGYNTPADIWSTACMAFELATGDYLFEPHSGEEYTRDEDHIALIIELLGKVPRKLIVAGKYSKEFFTKKGDLKHITKLKPWGLFEVLVEKYEWSQEEAAGFTDFLLPMLELIPEKRATAAECLRHPWLNS<pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad>']

Substrate Substrate_Acc   Motif_Sequence  position   Kinase Kinase_Acc  \
2925       NaN        Q96SB4  DYLFEPHSGEEYTRD       726  CSNK2A2     P19784   
2926       NaN        Q96SB4  DYLFEPHSGEEYTRD       726  CSNK2A1     P68400   

     kinase_group kinase_family kinase_sub_family  binding_domain  \
2925         CMGC           CK2               NaN             NaN   
2926         CMGC           CK2               NaN             NaN   

      taxonomy_id  species_name   db_source  SIGNOR_Score  \
2925         9606  Homo sapiens  phosphoELM           NaN   
2926         9606  Homo sapiens  phosphoELM           NaN   

                                          Full_Sequence  \
2925  MERKVLALQARKKRTKAKKDKAQRKSETQHRGSAPHSESDLPEQEE...   
2926  MERKVLALQARKKRTKAKKDKAQRKSETQHRGSAPHSESDLPEQEE...   

                                       centered_sub_seq  
2925  ENILLSVNEQYIRRLAAEATEWQRSGAPPPSGSAVSTAPQPKPADK...  
2926  ENILLSVNEQYIRRLAAEATEWQRSGAPPPSGSAVSTAPQPKPADK...

In [238]:
dfload.iloc[2925] #this position is outside of the length of the sequence????

Substrate                                                       POLR2A
Substrate_Acc                                                   P08775
Motif_Sequence                                         SPSSPEYTPASPKYS
position                                                          1854
Kinase                                                           CDK13
Kinase_Acc                                                      Q14004
kinase_group                                                      CMGC
kinase_family                                                      CDK
kinase_sub_family                                                 CRK7
binding_domain                                                     NaN
taxonomy_id                                                       9606
species_name                                                       NaN
db_source                                                       SIGNOR
SIGNOR_Score                                                     0.556
Full_S

In [255]:
dfall3["Full_Sequence"][(dfall3["position"]==726)&(dfall3["Substrate_Acc"]=="Q96SB4")].str.len()

3460    655
3461    655
Name: Full_Sequence, dtype: int64

In [246]:
dfload["Full_Sequence"][dfload["position"]==1854].str.len()

3829    1970
4812    1970
5585    1970
6202    1970
Name: Full_Sequence, dtype: int64

In [266]:
dfload[(dfload["position"]>dfload["Full_Sequence"].str.len())] #these positions are outside of the sequence >.>

Substrate Substrate_Acc   Motif_Sequence  position   Kinase Kinase_Acc  \
2925        NaN        Q96SB4  DYLFEPHSGEEYTRD       726  CSNK2A2     P19784   
2926        NaN        Q96SB4  DYLFEPHSGEEYTRD       726  CSNK2A1     P68400   
3151     PTPN11        P35235  GLMQQQRSFR_____       595    PRKCA     P17252   
3678       BRAF        P28028  YACASPKTPIQAGGY       790    MAPK3     P27361   
4574     PTPN11        P35235  GLMQQQRSFR_____       595    PRKCH     P24723   
6535     PTPN11        P35235  GLMQQQRSFR_____       595     PKCB     P05771   
38987       NaN        Q93008  GQRAQENYEGSEEVS      2556    EPHB3     P54753   
39715       NaN        Q93008  GQRAQENYEGSEEVS      2556    EPHA3     P29320   
39999       NaN        Q93008  GQRAQENYEGSEEVS      2556     EGFR     P00533   

      kinase_group kinase_family kinase_sub_family  binding_domain  \
2925          CMGC           CK2               NaN             NaN   
2926          CMGC           CK2               NaN             NaN   
3151           AGC           PKC              PKCA             NaN   
3678          CMGC          MAPK              ERK1             NaN   
4574           AGC           PKC              PKCH             NaN   
6535           AGC           PKC              PKCA             NaN   
38987           TK           EPH               NaN             NaN   
39715           TK           EPH               NaN             NaN   
39999           TK          EGFR               NaN             NaN   

       taxonomy_id  species_name    db_source  SIGNOR_Score  \
2925          9606  Homo sapiens   phosphoELM           NaN   
2926          9606  Homo sapiens   phosphoELM           NaN   
3151          9606           NaN       SIGNOR         0.329   
3678          9606           NaN       SIGNOR         0.630   
4574          9606           NaN       SIGNOR         0.313   
6535          9606           NaN       SIGNOR         0.336   
38987         9606           NaN  KINASE-iKiP           NaN   
39715         9606           NaN  KINASE-iKiP           NaN   
39999         9606           NaN  KINASE-iKiP           NaN   

                                           Full_Sequence  \
2925   MERKVLALQARKKRTKAKKDKAQRKSETQHRGSAPHSESDLPEQEE...   
2926   MERKVLALQARKKRTKAKKDKAQRKSETQHRGSAPHSESDLPEQEE...   
3151   MTSRRWFHPNITGVEAENLLLTRGVDGSFLARPSKSNPGDFTLSVR...   
3678   MAALSGGGGSSSGGGGGGGGGGGGGDGGGGAEQGQALFNGDMEPEA...   
4574   MTSRRWFHPNITGVEAENLLLTRGVDGSFLARPSKSNPGDFTLSVR...   
6535   MTSRRWFHPNITGVEAENLLLTRGVDGSFLARPSKSNPGDFTLSVR...   
38987  MTATTRGSPVGGNDNQGQAPDGQSQPPLQQNQTSSPDSSNENSPAT...   
39715  MTATTRGSPVGGNDNQGQAPDGQSQPPLQQNQTSSPDSSNENSPAT...   
39999  MTATTRGSPVGGNDNQGQAPDGQSQPPLQQNQTSSPDSSNENSPAT...   

                                        centered_sub_seq  
2925   ENILLSVNEQYIRRLAAEATEWQRSGAPPPSGSAVSTAPQPKPADK...  
2926   ENILLSVNEQYIRRLAAEATEWQRSGAPPPSGSAVSTAPQPKPADK...  
3151   GQLKEKNGDVIELKYPLNCADPTSERWFHGHLSGKEAEKLLTEKGK...  
3678   HHPVPQEEASFPETALPSGSSSAPPSDSTGPQILTSPSPSKSIPIP...  
4574   GQLKEKNGDVIELKYPLNCADPTSERWFHGHLSGKEAEKLLTEKGK...  
6535   GQLKEKNGDVIELKYPLNCADPTSERWFHGHLSGKEAEKLLTEKGK...  
38987  LAARFLFTTGFHTKKVVRGSASDWYDALCILLRHSKNVRFWFAHNV...  
39715  LAARFLFTTGFHTKKVVRGSASDWYDALCILLRHSKNVRFWFAHNV...  
39999  LAARFLFTTGFHTKKVVRGSASDWYDALCILLRHSKNVRFWFAHNV...

In [ ]:
#some entries give you a position and a substrate accession but when i query the accession and get the sequence, it happens that for whatever reason they were referring to a different sequence (wrong isoforms, outdated sequences etc.)
#to make sure the position is actually correct, compare the position to the position in the full sequence #example line 27145 in phosphoelm dataset
def safe_index(row):
    try:
        return row["Full_Sequence"][row["position"]-1]
    except IndexError:
        return None  # or np.nan
print((dfload.apply(safe_index, axis=1)=="Y")|(dfload.apply(safe_index, axis=1)=="S")|(dfload.apply(safe_index, axis=1)=="T")) #generate masking sequence for all cases where my position is wrong
positionmask=(dfload.apply(safe_index, axis=1)=="Y")|(dfload.apply(safe_index, axis=1)=="S")|(dfload.apply(safe_index, axis=1)=="T")

0        True
1        True
3        True
4        True
5        True
         ... 
46680    True
46681    True
46682    True
46683    True
46684    True
Length: 45483, dtype: bool


In [296]:
dfload_fixed_positions=dfload[positionmask]

In [297]:
dfload_fixed_positions.to_csv("deduplicated_human_fullSeq_centered_filteredpos.tsv",sep="\t",index=False)

In [299]:
unique_sequences=list(dfload_fixed_positions["centered_sub_seq"].unique())
len(unique_sequences)

18308

In [15]:
##deal with jak2 mouse kinase, center it on domain 1 and domain 2
dfkinmload=pd.read_csv("/run/user/1000/gvfs/smb-share:server=130.92.40.167,share=guest/Tim/Scripts/TreeData/MouseKinomeSeqFamilyClassification_centered_15substrates.csv")

In [27]:
#domaincenter for the kinase in position 1 is: 677 • that of kinase domain 2:  976
dfkinmload


dfkinmloadjak2_1=dfkinmload.copy()
dfkinmloadjak2_1.loc[dfkinmloadjak2_1["Kinase"]=="JAK2", "Centered_Kinase_Sequence"]=take_position(dfkinmloadjak2_1.loc[dfkinmloadjak2_1["Kinase"]=="JAK2","Sequence"].values[0],677,length=1021)

dfkinmloadjak2_2=dfkinmload.copy()
dfkinmloadjak2_2.loc[dfkinmloadjak2_2["Kinase"]=="JAK2", "Centered_Kinase_Sequence"]=take_position(dfkinmloadjak2_2.loc[dfkinmloadjak2_2["Kinase"]=="JAK2","Sequence"].values[0],976,length=1021)

In [30]:
dfkinmloadjak2_1.to_csv("TreeData/MouseKinomeSeqFamilyClassification_centered_onJAK21_15substrates.csv",index=False)
dfkinmloadjak2_2.to_csv("TreeData/MouseKinomeSeqFamilyClassification_centered_onJAK22_15substrates.csv",index=False)

In [ ]:
#also change centering on the human kinases that have 2 domains to not be in the middle but rather on one of the domains (choice for jak family is justified from uniprot, choice of the RPS6KA_ kinases not so much)

hukinload=pd.read_csv("/run/user/1000/gvfs/smb-share:server=130.92.40.167,share=guest/Tim/Scripts/TreeData/HumanKinomeSeqFamilyClassification_centered_20substrates.csv")

In [35]:
hukinload

Unnamed: 0     xName Manning Name  HGNC Name   \
0             1     ABL1           ABL       ABL1    
1             2     ABL2           ARG       ABL2    
2             4      ACK           ACK       TNK2    
3             5    ACTR2         ACTR2     ACVR2A    
4            12     AKT1          AKT1       AKT1    
..          ...       ...           ...        ...   
296         530     p38d          p38d     MAPK13    
297         531     p38g          p38g     MAPK12    
298         532   p70S6K        p70S6K    RPS6KB1    
299         533  p70S6Kb       p70S6Kb    RPS6KB2    
300         534   skMLCK        skMLCK      MYLK2    

                                   Kinase Name  Group  Family  SubFamily   \
0                 Tyrosine-protein kinase ABL1     TK     Abl         NaN   
1            Abelson tyrosine-protein kinase 2     TK     Abl         NaN   
2                     Activated CDC42 kinase 1     TK     Ack         NaN   
3                     Activin receptor type-2A    TKL    STKR      STKR2    
4    RAC-alpha serine/threonine-protein kinase    AGC     Akt         NaN   
..                                          ...    ...     ...        ...   
296        Mitogen-activated protein kinase 13   CMGC    MAPK        p38    
297        Mitogen-activated protein kinase 12   CMGC    MAPK        p38    
298         Ribosomal protein S6 kinase beta-1    AGC     RSK     RSKp70    
299         Ribosomal protein S6 kinase beta-2    AGC     RSK     RSKp70    
300                Myosin light chain kinase 2   CAMK    MLCK         NaN   

    UniprotID                                    Kinase_Sequence  \
0      P00519  MLEICLKLVGCKSKKGLSSSSSCYLEEALQRPVASDFEPQGLSEAA...   
1      P42684  MGQQVGRVGEAPGLQQPQPRGIRGSSAARPSGRRRDPAGRTTETGF...   
2      Q07912  MQPEEGTGWLLELLSEVQLQQYFLRLRDDLNVTRLSHFEYVKNEDL...   
3      P27037  MGAAAKLAFAVFLISCSSGAILGRSETQECLFFNANWEKDRTNQTG...   
4      P31749  MSDVAIVKEGWLHKRGEYIKTWRPRYFLLKNDGTFIGYKERPQDVD...   
..        ...                                                ...   
296    O15264  MSLIRKKGFYKQDVNKTAWELPKTYVSPTHVGSGAYGSVCSAIDKR...   
297    P53778  MSSPPPARSGFYRQEVTKTAWEVRAVYRDLQPVGSGAYGAVCSAVD...   
298    P23443  MRRRRRRDGFYPAPDFRDREAEDMAGVFDIDLDQPEDAGSEDELEE...   
299    Q9UBS0  MAAVFDLDLETEEGSEGEGEPELSPADACPLAELRAAGLEPVGHYE...   
300    Q9H1R3  MATENGAVELGIQNPSTDKAPKGPTGERPLAAGKDPGPPDPKKAPD...   

           Domain  Domaincenters  \
0    [(242, 493)]            367   
1    [(288, 539)]            413   
2    [(126, 385)]            255   
3    [(192, 485)]            338   
4    [(150, 408)]            279   
..            ...            ...   
296   [(25, 308)]            166   
297   [(27, 311)]            169   
298   [(91, 352)]            221   
299   [(67, 328)]            197   
300  [(285, 540)]            412   

                              Centered_Kinase_Sequence  
0    <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
1    <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
2    <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
3    <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
4    <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
..                                                 ...  
296  <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
297  <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
298  <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
299  <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
300  <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  

[301 rows x 13 columns]

In [43]:
hkl=hukinload.copy()




hkl.loc[hkl["HGNC Name "]=="JAK1 ", "Centered_Kinase_Sequence"]=take_position(hkl.loc[hkl["HGNC Name "]=="JAK1 ","Kinase_Sequence"].values[0],(875+1153)//2,length=1021)
hkl.loc[hkl["HGNC Name "]=="JAK2 ", "Centered_Kinase_Sequence"]=take_position(hkl.loc[hkl["HGNC Name "]=="JAK2 ","Kinase_Sequence"].values[0],(849+1124)//2,length=1021)
hkl.loc[hkl["HGNC Name "]=="JAK3 ", "Centered_Kinase_Sequence"]=take_position(hkl.loc[hkl["HGNC Name "]=="JAK3 ","Kinase_Sequence"].values[0],(822+1111)//2,length=1021)
hkl.loc[hkl["HGNC Name "]=="TYK2 ", "Centered_Kinase_Sequence"]=take_position(hkl.loc[hkl["HGNC Name "]=="TYK2 ","Kinase_Sequence"].values[0],(897+1176)//2,length=1021)
hkl.loc[hkl["HGNC Name "]=="RPS6KA5 ", "Centered_Kinase_Sequence"]=take_position(hkl.loc[hkl["HGNC Name "]=="RPS6KA5 ","Kinase_Sequence"].values[0],(426+687)//2,length=1021)
hkl.loc[hkl["HGNC Name "]=="RPS6KA4 ", "Centered_Kinase_Sequence"]=take_position(hkl.loc[hkl["HGNC Name "]=="RPS6KA4 ","Kinase_Sequence"].values[0],(411+674)//2,length=1021)
hkl.loc[hkl["HGNC Name "]=="RPS6KA1 ", "Centered_Kinase_Sequence"]=take_position(hkl.loc[hkl["HGNC Name "]=="RPS6KA1 ","Kinase_Sequence"].values[0],(418+675)//2,length=1021)
hkl.loc[hkl["HGNC Name "]=="RPS6KA3 ", "Centered_Kinase_Sequence"]=take_position(hkl.loc[hkl["HGNC Name "]=="RPS6KA3 ","Kinase_Sequence"].values[0],(422+679)//2,length=1021)
hkl.loc[hkl["HGNC Name "]=="RPS6KA2 ", "Centered_Kinase_Sequence"]=take_position(hkl.loc[hkl["HGNC Name "]=="RPS6KA2 ","Kinase_Sequence"].values[0],(415+672)//2,length=1021)
hkl.loc[hkl["HGNC Name "]=="RPS6KA6 ", "Centered_Kinase_Sequence"]=take_position(hkl.loc[hkl["HGNC Name "]=="RPS6KA6 ","Kinase_Sequence"].values[0],(426+683)//2,length=1021)

In [44]:
hkl.to_csv("TreeData/HumanKinomeSeqFamilyClassification_centered_20substrates_2domaincentered.csv",index=False)

In [45]:
hkl

Unnamed: 0     xName Manning Name  HGNC Name   \
0             1     ABL1           ABL       ABL1    
1             2     ABL2           ARG       ABL2    
2             4      ACK           ACK       TNK2    
3             5    ACTR2         ACTR2     ACVR2A    
4            12     AKT1          AKT1       AKT1    
..          ...       ...           ...        ...   
296         530     p38d          p38d     MAPK13    
297         531     p38g          p38g     MAPK12    
298         532   p70S6K        p70S6K    RPS6KB1    
299         533  p70S6Kb       p70S6Kb    RPS6KB2    
300         534   skMLCK        skMLCK      MYLK2    

                                   Kinase Name  Group  Family  SubFamily   \
0                 Tyrosine-protein kinase ABL1     TK     Abl         NaN   
1            Abelson tyrosine-protein kinase 2     TK     Abl         NaN   
2                     Activated CDC42 kinase 1     TK     Ack         NaN   
3                     Activin receptor type-2A    TKL    STKR      STKR2    
4    RAC-alpha serine/threonine-protein kinase    AGC     Akt         NaN   
..                                          ...    ...     ...        ...   
296        Mitogen-activated protein kinase 13   CMGC    MAPK        p38    
297        Mitogen-activated protein kinase 12   CMGC    MAPK        p38    
298         Ribosomal protein S6 kinase beta-1    AGC     RSK     RSKp70    
299         Ribosomal protein S6 kinase beta-2    AGC     RSK     RSKp70    
300                Myosin light chain kinase 2   CAMK    MLCK         NaN   

    UniprotID                                    Kinase_Sequence  \
0      P00519  MLEICLKLVGCKSKKGLSSSSSCYLEEALQRPVASDFEPQGLSEAA...   
1      P42684  MGQQVGRVGEAPGLQQPQPRGIRGSSAARPSGRRRDPAGRTTETGF...   
2      Q07912  MQPEEGTGWLLELLSEVQLQQYFLRLRDDLNVTRLSHFEYVKNEDL...   
3      P27037  MGAAAKLAFAVFLISCSSGAILGRSETQECLFFNANWEKDRTNQTG...   
4      P31749  MSDVAIVKEGWLHKRGEYIKTWRPRYFLLKNDGTFIGYKERPQDVD...   
..        ...                                                ...   
296    O15264  MSLIRKKGFYKQDVNKTAWELPKTYVSPTHVGSGAYGSVCSAIDKR...   
297    P53778  MSSPPPARSGFYRQEVTKTAWEVRAVYRDLQPVGSGAYGAVCSAVD...   
298    P23443  MRRRRRRDGFYPAPDFRDREAEDMAGVFDIDLDQPEDAGSEDELEE...   
299    Q9UBS0  MAAVFDLDLETEEGSEGEGEPELSPADACPLAELRAAGLEPVGHYE...   
300    Q9H1R3  MATENGAVELGIQNPSTDKAPKGPTGERPLAAGKDPGPPDPKKAPD...   

           Domain  Domaincenters  \
0    [(242, 493)]            367   
1    [(288, 539)]            413   
2    [(126, 385)]            255   
3    [(192, 485)]            338   
4    [(150, 408)]            279   
..            ...            ...   
296   [(25, 308)]            166   
297   [(27, 311)]            169   
298   [(91, 352)]            221   
299   [(67, 328)]            197   
300  [(285, 540)]            412   

                              Centered_Kinase_Sequence  
0    <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
1    <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
2    <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
3    <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
4    <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
..                                                 ...  
296  <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
297  <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
298  <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
299  <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  
300  <pad><pad><pad><pad><pad><pad><pad><pad><pad><...  

[301 rows x 13 columns]